In [1]:
import csv 
import numpy as np
infile = open("/Users/stefano_savian/Desktop/social_data_ass/NYPD_Motor_Vehicle_Collisions.csv", 'r')
data = csv.reader(infile, delimiter = ',')
inc = {}
incidentlist = []


for row in data:   
    inc ={'BOROUGH': row[2], 'LATITUDE':row[4], 'LONGITUDE':row[5], 'LOCATION':row[6], 
          'NUMBER OF PERSONS KILLED':row[11], 'CONTRIBUTING FACTOR VEHICLE 1':row[18], 
          'CONTRIBUTING FACTOR VEHICLE 2':row[19],'CONTRIBUTING FACTOR VEHICLE 3':row[20],
          'CONTRIBUTING FACTOR VEHICLE 4':row[21],   'CONTRIBUTING FACTOR VEHICLE 5':row[22],
          'VEHICLE TYPE CODE 1':row[24], 'VEHICLE TYPE CODE 2':row[25],'VEHICLE TYPE CODE 3':row[26],
          'VEHICLE TYPE CODE 4':row[27], 'VEHICLE TYPE CODE 5':row[28], 'TIME': row[1], 'NUMBER OF PERSONS INJURED': row[10]
         }
                                                
    incidentlist.append(inc)
    
headers = headers = ['DATE', 'TIME', 'BOROUGH', 'ZIP CODE', 'LATITUDE', 'LONGITUDE', 'LOCATION', 'ON STREET NAME', 
                     'CROSS STREET NAME', 'OFF STREET NAME', 'NUMBER OF PERSONS INJURED', 'NUMBER OF PERSONS KILLED',
                     'NUMBER OF PEDESTRIANS INJURED', 'NUMBER OF PEDESTRIANS KILLED', 'NUMBER OF CYCLIST INJURED', 
                     'NUMBER OF CYCLIST KILLED', 'NUMBER OF MOTORIST INJURED', 'NUMBER OF MOTORIST KILLED', 
                     'CONTRIBUTING FACTOR VEHICLE 1', 'CONTRIBUTING FACTOR VEHICLE 2', 'CONTRIBUTING FACTOR VEHICLE 3', 
                     'CONTRIBUTING FACTOR VEHICLE 4', 'CONTRIBUTING FACTOR VEHICLE 5', 'UNIQUE KEY', 'VEHICLE TYPE CODE 1',
                     'VEHICLE TYPE CODE 2', 'VEHICLE TYPE CODE 3', 'VEHICLE TYPE CODE 4', 'VEHICLE TYPE CODE 5']

In [2]:
print incidentlist[0]
incidentlist = incidentlist[1:]
print incidentlist[0]

{'VEHICLE TYPE CODE 4': 'VEHICLE TYPE CODE 4', 'CONTRIBUTING FACTOR VEHICLE 1': 'CONTRIBUTING FACTOR VEHICLE 1', 'CONTRIBUTING FACTOR VEHICLE 2': 'CONTRIBUTING FACTOR VEHICLE 2', 'CONTRIBUTING FACTOR VEHICLE 3': 'CONTRIBUTING FACTOR VEHICLE 3', 'CONTRIBUTING FACTOR VEHICLE 4': 'CONTRIBUTING FACTOR VEHICLE 4', 'CONTRIBUTING FACTOR VEHICLE 5': 'CONTRIBUTING FACTOR VEHICLE 5', 'VEHICLE TYPE CODE 2': 'VEHICLE TYPE CODE 2', 'NUMBER OF PERSONS KILLED': 'NUMBER OF PERSONS KILLED', 'VEHICLE TYPE CODE 3': 'VEHICLE TYPE CODE 3', 'LONGITUDE': 'LONGITUDE', 'VEHICLE TYPE CODE 5': 'VEHICLE TYPE CODE 5', 'LOCATION': 'LOCATION', 'TIME': 'TIME', 'LATITUDE': 'LATITUDE', 'NUMBER OF PERSONS INJURED': 'NUMBER OF PERSONS INJURED', 'BOROUGH': 'BOROUGH', 'VEHICLE TYPE CODE 1': 'VEHICLE TYPE CODE 1'}
{'VEHICLE TYPE CODE 4': '', 'CONTRIBUTING FACTOR VEHICLE 1': 'Unspecified', 'CONTRIBUTING FACTOR VEHICLE 2': 'Unspecified', 'CONTRIBUTING FACTOR VEHICLE 3': '', 'CONTRIBUTING FACTOR VEHICLE 4': '', 'CONTRIBUTING F

In [3]:
car1 = map(lambda x: x.get('VEHICLE TYPE CODE 1'), incidentlist)   
car2 = map(lambda x: x.get('VEHICLE TYPE CODE 2'), incidentlist)
car3 = map(lambda x: x.get('VEHICLE TYPE CODE 3'), incidentlist)
car4 = map(lambda x: x.get('VEHICLE TYPE CODE 4'), incidentlist)
car5 = map(lambda x: x.get('VEHICLE TYPE CODE 5'), incidentlist)

car1 = set(car1)
car2 = set(car2)
car3 = set(car3)
car4 = set(car4)
car5 = set(car5)
car_types = filter(None, car1.union(car2, car3, car4, car5))
categories = map(lambda x: x, car_types)

categories = list(categories)


In [4]:
a = map(lambda x: x.get('TIME') ,incidentlist)
print a[0:10]
print int(a[0].split(":")[0])
#b = int( a.split("/")[-1] )
print 

['0:45', '2:40', '3:27', '2:00', '0:10', '13:20', '16:50', '3:51', '16:55', '17:00']
0



In [5]:
features = []
for item in incidentlist:
    
    car_types = [0 for a in range(len(categories))]
    if item.get('VEHICLE TYPE CODE 1'):
        car_types[categories.index(item.get('VEHICLE TYPE CODE 1'))] = 1
    if item.get('VEHICLE TYPE CODE 2'):
        car_types[categories.index(item.get('VEHICLE TYPE CODE 2'))] = 1
    if item.get('VEHICLE TYPE CODE 3'):
        car_types[categories.index(item.get('VEHICLE TYPE CODE 3'))] = 1
    if item.get('VEHICLE TYPE CODE 4'):
        car_types[categories.index(item.get('VEHICLE TYPE CODE 4'))] = 1
    if item.get('VEHICLE TYPE CODE 5'):
        car_types[categories.index(item.get('VEHICLE TYPE CODE 5'))] = 1   
    lat = item.get('LATITUDE')
    lon = item.get('LONGITUDE')
    time = int(item.get('TIME').split(":")[0])
    if int(item.get('TIME').split(":")[1])>30:
        time = time + 1
    
    if lat and lon:
        lat, lon = float(lat), float(lon)
        features.append(car_types + [lat] + [lon] + [time])
        
    else:
        features.append(car_types + [0] + [0] + [time]) #for empty locations I added 0


In [18]:
target = map(lambda x: max(int(x.get('NUMBER OF PERSONS KILLED')),int(x.get('NUMBER OF PERSONS INJURED'))) , incidentlist)

#print (incidentlist[0].get('NUMBER OF PERSONS KILLED'))

def inj(i):
    if i>0:
        return True
    else:
        return False
boolean_target = map(lambda x:  inj(x), target )



In [7]:
from sklearn import neighbors
from sklearn.cross_validation import train_test_split

X_train, X_test, y_train, y_test = train_test_split(features, boolean_target, test_size=0.10)

In [8]:
from sklearn import tree
clf = tree.DecisionTreeClassifier()
clf = clf.fit(X_train, y_train)
predictions = clf.predict(X_test, y_test)
print clf.score(X_test,y_test)


0.762177203339


In [43]:
import random          
#from random import randrange, random

dangerous = filter(lambda x: x == True, boolean_target)
b_features =  []         #balanced features
b_target = []
index = []

for i in range(0, len(dangerous)):
    index = random.randint(0, len(features))       #GIORGOS, SOMETIMES IT SAYS LIST INED OUT OF RANGE!!!!!
    b_features.append(features[index])
    b_target.append(boolean_target[index])

clf1 = tree.DecisionTreeClassifier()            #train with all the dataset
clf1 = clf1.fit(b_features, b_target)

car_type = [0 for a in range(len(categories))]
car_type[categories.index('TAXI')] = 1               #choosen category taxy
acc_time = 15                                        #choosen time 

p_labels = []

for lat in lats:                                   
    for lon in longs:
        p_labels.append(car_type + [lat] + [lon] + [acc_time])
        
        
predictions = clf1.predict(p_labels)
a = filter(lambda x: x== True, predictions)


Tlat = []
Tlon = []
Flat = []
Flon = []
for i in range(0, len(predictions)):
    if predictions[i] == True:
        Tlat.append(p_labels[i][len(categories)])
        Tlon.append(p_labels[i][len(categories)+1])
    else:
        Flat.append(p_labels[i][len(categories)])
        Flon.append(p_labels[i][len(categories)+1])

red_loc = { 'lat': Tlat, 'lon': Tlon }
green_loc = { 'lat': Flat, 'lon': Flon }

print len(Tlat)

2620


In [44]:
import geoplotlib 
from geoplotlib.utils import BoundingBox

bbox = BoundingBox(north=40.944336, west= -74.291151,
                   south=40.467527, east= -73.686903)

longs = np.linspace(-73.700636,-74.254073, num=70)       # grid bounds
lats = np.linspace(40.496774, 40.918385, num=70)
geoplotlib.dot(red_loc, color = "red")               #prints grid
geoplotlib.dot(green_loc, color = "green") 
geoplotlib.set_bbox(bbox)
geoplotlib.inline()

In [61]:
clf1 = tree.DecisionTreeClassifier()            #train with all the dataset
clf1 = clf1.fit(b_features, b_target)

car_type = [0 for a in range(len(categories))]
car_type[categories.index('LARGE COM VEH(6 OR MORE TIRES)')] = 1               #choosen category taxy
acc_time = 17                                                                 #choosen time 

p_labels = []

for lat in lats:                                   
    for lon in longs:
        p_labels.append(car_type + [lat] + [lon] + [acc_time])
        
        
predictions = clf1.predict(p_labels)
a = filter(lambda x: x== True, predictions)


Tlat = []
Tlon = []
Flat = []
Flon = []
for i in range(0, len(predictions)):
    if predictions[i] == True:
        Tlat.append(p_labels[i][len(categories)])
        Tlon.append(p_labels[i][len(categories)+1])
    else:
        Flat.append(p_labels[i][len(categories)])
        Flon.append(p_labels[i][len(categories)+1])

red_loc = { 'lat': Tlat, 'lon': Tlon }
green_loc = { 'lat': Flat, 'lon': Flon }

print len(Tlat)

1436


In [62]:
bbox = BoundingBox(north=40.944336, west= -74.291151,
                   south=40.467527, east= -73.686903)

longs = np.linspace(-73.700636,-74.254073, num=70)       # grid bounds
lats = np.linspace(40.496774, 40.918385, num=70)
geoplotlib.dot(red_loc, color = "red")               #prints grid
geoplotlib.dot(green_loc, color = "green") 
geoplotlib.set_bbox(bbox)
geoplotlib.inline()

In [52]:
print categories

['TAXI', 'SMALL COM VEH(4 TIRES)', 'VAN', 'UNKNOWN', 'SCOOTER', 'SPORT UTILITY / STATION WAGON', 'OTHER', 'MOTORCYCLE', 'AMBULANCE', 'PASSENGER VEHICLE', 'PICK-UP TRUCK', 'BICYCLE', 'PEDICAB', 'BUS', 'LIVERY VEHICLE', 'FIRE TRUCK', 'LARGE COM VEH(6 OR MORE TIRES)']
